In [1]:
!pip install ordpy
import numpy as np
import ordpy
from ordpy import renyi_entropy
from ordpy import permutation_entropy
from ordpy import renyi_complexity_entropy
from ordpy import minimum_complexity_entropy
from ordpy import maximum_complexity_entropy
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import seaborn as sns
import string
import glob
import warnings
import math
from scipy.fft import fft, ifft
from scipy.io import savemat
import matplotlib.colors as mcolors
from mpl_toolkits.mplot3d import Axes3D

In [2]:
def maximum_renyi_complexity_entropy(dx=3, dy=1, m=1, q=1.4):
    """
    Generates data corresponding to values of normalized renyi permutation
    entropy and statistical complexity which delimit the upper boundary in the
    complexity-entropy renyi causality plane\\ [#rosso_curvas]_:sup:`,`\\ [*]_.

    Parameters
    ----------
    dx : int
         Embedding dimension (horizontal axis) (default: 3).
    dy : int
         Embedding dimension (vertical axis); must be 1 for time series
         (default: 1).
    m : int
        The length of the returned array containing values of permutation entropy
        and statistical complexity is given by
        :math:`[(d_x \\times d_y)!-1] \\times m`.
    q:  float
        Renyi parameter (default: 1.4)

    Returns
    -------
     : array
       Values of normalized permutation entropy and statistical complexity
       belonging to the upper limiting curve of the complexity-entropy causality
       plane.

    Notes
    -----
    .. [*] This function was adapted from Ordpy.

    """
    if q==1.0:
       return maximum_complexity_entropy(dx,dy,m)
    else:
       N              = math.factorial(dx*dy)
       hlist_, clist_ = np.zeros(shape=(N-1,m)), np.zeros(shape=(N-1,m))
       for i in range(N-1):
           p             = np.zeros(shape=N)
           uniform_dist  = np.full(N, 1/N)
           prob_params   = np.linspace(0, 1/N, num=m)
           for k in range(len(prob_params)):
               p[0] = prob_params[k]
               for j in range(1,N-i):
                   p[j] = (1-prob_params[k])/(N-i-1)
               h = renyi_entropy(p,q,dx, dy, probs=True)
               p_plus_u_over_2      = (uniform_dist + p)/2
               s_of_p_plus_u_over_2 = renyi_entropy(p_plus_u_over_2,q,dx, dy, probs=True)
               p_non_zero    = p[p!=0]
               p_plus_u_over_2_no      = (1/N + p_non_zero)/2
               t_1=np.log(sum((p**q)*p_plus_u_over_2**(1-q)))
               t_2=np.log(sum((uniform_dist**q)*p_plus_u_over_2**(1-q)))
               js_div_max = (0.5/(q-1))*np.log((((N+1)**(1-q)+N-1)/N)*((N+1)/(4*N))**(1-q))
               js_div     = (0.5/(q-1))*(t_1+t_2)
               hlist_[i, k] = h
               clist_[i, k] = h*js_div/js_div_max

       #flatenning the arrays and ordering the pairs of values.
       hlist_ = hlist_.flatten()
       clist_ = clist_.flatten()
       args   = np.argsort(hlist_)

    return np.asarray((hlist_[args], clist_[args])).T

In [3]:
def minimum_renyi_complexity_entropy(dx=3, dy=1, size=100,q=1.4):
    """
    Generates data corresponding to values of normalized renyi permutation
    entropy and statistical complexity which delimit the lower boundary in the
    complexity-entropy renyi causality plane\\ [#rosso_curvas]_:sup:`,`\\ [*]_.

    Parameters
    ----------
    dx : int
         Embedding dimension (horizontal axis) (default: 3).
    dy : int
         Embedding dimension (vertical axis); must be 1 for time series
         (default: 1).
    size : int
           The length of the array returned containing pairs of values of
           permutation entropy and statistical complexity.
    q:  float
        Renyi parameter (default: 1.4)

    Returns
    -------
     : array
       Values of normalized permutation entropy and statistical complexity
       belonging to the lower limiting curve of the complexity-entropy
       causality plane.

    Notes
    -----
    .. [*] This function was adapted from Ordpy.

    """
    if q==1.0:
       return minimum_complexity_entropy(dx,dy,size)
    else:
       size        += 1
       N            = math.factorial(dx*dy)
       prob_params  = np.linspace(1/N, 1, num=size-1)
       uniform_dist = np.full(N, 1/N)
       hc_ = []
       for i in range(size-1):
           probabilities    = np.full(shape=N, fill_value=(1-prob_params[i])/(N-1))
           probabilities[0] = prob_params[i]
           h = renyi_entropy(probabilities,q,dx, dy, probs=True)
           p_plus_u_over_2      = (uniform_dist + probabilities)/2
           s_of_p_plus_u_over_2 = renyi_entropy(p_plus_u_over_2,q,dx, dy, probs=True)
           # probabilities = probabilities[probabilities!=0]

           t_1=np.log(sum((probabilities**q)*p_plus_u_over_2**(1-q)))
           t_2=np.log(sum((uniform_dist**q)*p_plus_u_over_2**(1-q)))

           js_div_max = (0.5/(q-1))*np.log((((N+1)**(1-q)+N-1)/N)*((N+1)/(4*N))**(1-q))
           js_div     = (0.5/(q-1))*(t_1+t_2)


           hc_.append([h, h*js_div/js_div_max])

       return np.flip(hc_, axis=0)


In [4]:
D = 5  # Bandt and Pompe dimension
m = 100  #increase for smaller D
size = 719

q_values = np.array([0.5, 0.7, 1, 1.4, 2, 3, 4, 5, 6, 7])

# Create empty lists to store all h and c values
hmin_values = []
cmin_values = []
hmax_values = []
cmax_values = []

for q in q_values:
    # Compute minimum Renyi complexity and entropy
    hmin, cmin = minimum_renyi_complexity_entropy(dx=D, size=size, q=q).T
    # Compute maximum Renyi complexity and entropy
    hmax, cmax = maximum_renyi_complexity_entropy(dx=D, m=m, q=q).T

    # Append values to the lists
    hmin_values.append(hmin)
    cmin_values.append(cmin)
    hmax_values.append(hmax)
    cmax_values.append(cmax)

# Convert the lists to numpy arrays to use them in plot_surface
hmin_values = np.array(hmin_values)
cmin_values = np.array(cmin_values)
hmax_values = np.array(hmax_values)
cmax_values = np.array(cmax_values)




In [5]:
import scipy.io as sio

# Prepare data dictionary
data = {
    'hmin_values': hmin_values,
    'cmin_values': cmin_values,
    'hmax_values': hmax_values,
    'cmax_values': cmax_values,
    'q_values': q_values
}

# Save the data to a .mat file in case you want to use it in MATLAB
sio.savemat('dataD5.mat', data)



In [7]:
import plotly.graph_objects as go
import numpy as np
import fractions

# Compute the vector and its logarithm
vector = 1/q_values
vector2 = np.log(vector)

# Generate labels for q values
labels = [str(int(i)) if i.is_integer() else str(i) for i in q_values]

# Set axis titles
x_axis_title = 'q'
y_axis_title = 'H<sub>q</sub>'
z_axis_title = 'C<sub>q</sub>'

# Create a 3D figure
fig = go.Figure()

# Add traces for minimum values of h
for i in range(hmin_values.shape[0]):
    fig.add_trace(go.Scatter3d(x=[np.log(1/q_values[i])]*hmin_values.shape[1], y=hmin_values[i, :], z=cmin_values[i, :], mode='lines', line=dict(color='skyblue'), showlegend=False))

# Add traces for maximum values of h
for i in range(hmax_values.shape[0]):
    fig.add_trace(go.Scatter3d(x=[np.log(1/q_values[i])]*hmax_values.shape[1], y=hmax_values[i, :], z=cmax_values[i, :], mode='lines', line=dict(color='salmon'), showlegend=False))

# Add placeholders for legend
fig.add_trace(go.Scatter3d(x=[None], y=[None], z=[None], mode='lines', line=dict(color='skyblue'), name='C<sub>q</sub><sup>min</sup>'))
fig.add_trace(go.Scatter3d(x=[None], y=[None], z=[None], mode='lines', line=dict(color='salmon'), name='C<sub>q</sub><sup>max</sup>'))

# Customize the layout
fig.update_layout(scene=dict(
                    aspectmode='manual',
                    aspectratio=dict(x=1.3, y=1, z=0.7),  # Adjust the aspect ratio here
                    xaxis=dict(
                        tickmode='array',
                        tickvals=vector2,
                        ticktext=labels,
                        title=x_axis_title),
                    yaxis_title=y_axis_title,
                    zaxis_title=z_axis_title),
                  width=1200, height=1000,  # Adjust the figure size
                  showlegend=True,  # Show legend
                  scene_camera=dict(
                      eye=dict(x=1.2, y=-1.7, z=0.4),  # Adjust camera position
                      up=dict(x=0, y=0, z=1)),  # Define 'up' direction
                  legend=dict(
                      yanchor="top",
                      y=0.99,
                      xanchor="left",
                      x=0.01
                    ))

# Show the figure
fig.show()

